In [5]:


from transformers import AutoTokenizer, AutoModel
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import torch
import pandas as pd


data = np.load('embeddings.npy')
movies = pd.read_csv('data.csv')

def get_embeddings():
    tokenizer = AutoTokenizer.from_pretrained("cointegrated/rubert-tiny2")
    model = AutoModel.from_pretrained("cointegrated/rubert-tiny2")
    # model.cuda()  
    return model, tokenizer

def embed_bert_cls(text ):
    model, tokenizer = get_embeddings()
    t = tokenizer(text, padding=True, truncation=True, return_tensors='pt')
    with torch.no_grad():
        model_output = model(**{k: v.to(model.device) for k, v in t.items()})
    embeddings = model_output.last_hidden_state[:, 0, :]
    embeddings = torch.nn.functional.normalize(embeddings)
    return embeddings[0].cpu().numpy()

def top_indices(array, n):

    sorted_indices = np.argsort(array)[::-1]
    # Выбираем первые n индексов
    top_n_indices = sorted_indices[:n]
    return top_n_indices


def predict_rating(input_search):

    emb = embed_bert_cls(input_search)
    X=np.column_stack((data, np.tile(emb, (data.shape[0], 1))))


    # from catboost import CatBoostRanker
    # cb= CatBoostRanker()
    # cb.load_model('model.cbm')
    # y = cb.predict(X)

    # import pickle
    # with open('logreg.pkl', 'rb') as f:
    #     logreg = pickle.load(f)
    # y = logreg.predict(X)

    y= cosine_similarity(data, emb.reshape(1, -1)).reshape(-1)

    return top_indices(y, 10)


preds=predict_rating("Пока Мстители и их союзники продолжают защищать мир от различных опасностей, с которыми не смог бы справиться один супергерой, новая угроза возникает из космоса: Танос. Межгалактический тиран преследует цель ")

movies.iloc[preds]

name  \
28               Мстители: Война бесконечности   
4286         LEGO Мстители Марвел: Код красный   
13384  Могучие рейнджеры: Потерянная галактика   
2609                          Стражи терракоты   
1156                       Царство падальщиков   
3907      Железный человек и Халк: Союз героев   
27972           Потерянное львиное королевство   
297          Мир Юрского периода 3: Господство   
7626                                    Лузеры   
25332                          Ancestral World   

                                             description  \
28      В то время как отважные Мстители с союзниками...   
4286    Супергерои объединяются, чтобы противостоять ...   
13384   Казалось бы всё зло уже побеждено, однако в н...   
2609    Стражи волшебной Терракоты и магические сущес...   
1156    Грузовой корабль «Деметра» терпит аварию на н...   
3907    Когда питающийся электричеством и неуязвимый ...   
27972   Мультфильм о борьбе добра со злом на простора...   
297     Катастрофическое извержение вулкана Сибо на И...   
7626    «Лузеры» – сумасшедший экшн о предательстве и...   
25332   Пытаясь спасти своего брата и королевство сво...   

                                                    link    year  imdb   kp  \
28     https://www.lordfilm.bot/3670-mstiteli-vojna-b...  2018.0   8.4  8.1   
4286   https://www.lordfilm.bot/49932-lego-mstiteli-m...  2023.0   NaN  NaN   
13384  https://www.lordfilm.bot/18827-moguchie-rejndz...  1999.0   6.8  4.2   
2609   https://www.lordfilm.bot/46847-strazhi-terrako...  2021.0   6.2  6.7   
1156   https://www.lordfilm.bot/49892-carstvo-padalsc...  2023.0   8.8  NaN   
3907   https://www.lordfilm.bot/21296-zheleznyj-chelo...  2013.0   4.6  4.2   
27972  https://www.lordfilm.bot/24407-poterjannoe-lvi...  2019.0   3.8  NaN   
297    https://www.lordfilm.bot/47499-mir-jurskogo-pe...  2022.0   5.6  5.7   
7626      https://www.lordfilm.bot/6139-luzery-2010.html  2010.0   6.2  6.3   
25332  https://www.lordfilm.bot/10306-ancestral-world...  2020.0   2.5  NaN   

                    country  age  \
28                      США  18+   
4286                    США   0+   
13384  США, Франция, Япония   0+   
2609                  Китай  12+   
1156                    США   0+   
3907                    США  12+   
27972                   США  18+   
297             США, Мальта  12+   
7626           США, Франция  16+   
25332                   США   0+   

                                                  actors  \
28     Роберт Дауни мл., Крис Хемсворт, Марк Руффало,...   
4286                                                 NaN   
13384  Арчи Као, Регги Ролли, Дэнни Славин, Серина Ви...   
2609                                            Тань Сяо   
1156   Вунми Моссаку, Алиа Шокат, Сунита Мани, Боб Ст...   
3907   Адриан Пасдар, Фред Таташиор, Ди Брэдли Бейкер...   
27972                            Kj Schrock, Сара Тейлор   
297    Крис Пратт, Брайс Даллас Ховард, Лора Дерн, Сэ...   
7626   Джеффри Дин Морган, Зои Салдана, Крис Эванс, И...   
25332  Jennifer Mischiati, Джо Морелли, Райан А. Филл...   

                                                  genres  \
28     Фильмы, Фильмы Marvel, Боевики, Приключения, Ф...   
4286                                         Мультфильмы   
13384                                            Сериалы   
2609                                         Мультфильмы   
1156                                         Мультфильмы   
3907                                         Мультфильмы   
27972                                        Мультфильмы   
297    Фильмы, 2022 год, Боевики, Приключения, Трилле...   
7626   Фильмы, Боевики, Детективы, Комедии, Криминаль...   
25332     Фильмы, Боевики, 2020 год, Фильмы про монстров   

                                                  poster  
28     https://www.lordfilm.bot/uploads/posts/2020-10...  
4286   https://www.lordfilm.bot/uploads/posts/2023-10...  
13384  https://www.lordfilm.bot/uploads/posts/2021-03...  
2609 